In [1]:
import pickle
from tqdm import tqdm
tqdm.pandas()
import pandas as pd
import plotly.offline as pyo
import plotly.express as px
import dimensionality_reduction
import json 
import random
from numpy import dot
from numpy.linalg import norm
import numpy as np
from utils import aggregate_embeddings, cosine_similarity, print_similarity_samples, replace_nan_with, load_model, load_big_consulting_export, split_into_list, load_ai_news, load_car_news

In [2]:
def get_embedding_dict(df, column):
    if isinstance(df[column].iloc[0], list):
        value_list = list(set().union(*df[column]))
    elif isinstance(df[column].iloc[0], str):
        value_list = list(set(df[column]))
    embedding_dict = {}
    for value in tqdm(value_list):
        embedding_dict[value] = sbert_model.encode(value)
        
    return embedding_dict

In [3]:
# merged_df.to_csv('snippet_similarity.tsv', sep='\t', index=False)
# train_df = pd.read_csv('../similarity-training-data/sbert-company/train.tsv', sep='\t')
sbert_model = load_model()
# big_consulting_df = load_big_consulting_export()
ai_news_df = load_ai_news()
car_news_df = load_car_news()
# df = pd.concat([big_consulting_df, ai_news_df, car_news_df], axis=0).reset_index(drop=True)
ai_news_df

replace   
0       Free Report #COMPANY provides cloud-native and...  \
1       Some additional features #COMPANY offers inclu...   
2       #COMPANY, an artificial intelligence-driven ph...   
3                  #COMPANY to stand apart from its peers   
4       #COMPANY is at the top of the pack in the arti...   
...                                                   ...   
262916  On #DATE, #COMPANY announced that #COMPANY has...   
262917  #COMPANY, a software company, has acquired #CO...   
262918  #COMPANY's Food AI brings together user prefer...   
262919  Announcing the achievement, the company said i...   
262920  #COMPANY has strained to meet demand for its A...   

                                                  snippet classification   
0       ( Get Free Report CS Disco, Inc provides cloud...        PRODUCT  \
1       Some additional features SoMee offers include ...         ENTITY   
2       Exscientia plc, an 1-driven pharmatech company...          STATE   
3       But what allows CrowdStrike to stand apart fro...         ENTITY   
4       Google is at the top of the pack in the 1 race...         ENTITY   
...                                                   ...            ...   
262916  On January 27, 2021, BenevolentAI announced th...         ENTITY   
262917  Visma, a software company, has acquired Provad...        ACQUIRE   
262918  Whisk's Food 1 brings together user preference...          OTHER   
262919  Announcing the achievement, the company said i...         ENTITY   
262920  Nvidia has strained to meet demand for its 1 c...          OTHER   

                          keywords  
0          artificial intelligence  
1                 ai|generative ai  
2          artificial intelligence  
3       ai|artificial intelligence  
4          artificial intelligence  
...                            ...  
262916                          ai  
262917                     chatbot  
262918                          ai  
262919                          ai  
262920                          ai  

[262523 rows x 4 columns]

In [6]:
import pandas as pd

def create_replace_no_tags_col(df):
    def remove_hashtags(text):
        words = text.split()
        words = [word for word in words if not word.startswith('#')]
        return ' '.join(words)
    df['replace_no_tags'] = df['replace'].apply(remove_hashtags)
    df['replace_no_tags'] = df['replace_no_tags'].str.replace(r'\s+', ' ')
    return df

ai_news_df = create_replace_no_tags_col(ai_news_df)
car_news_df = create_replace_no_tags_col(car_news_df)

In [7]:
# ai_news_df = split_into_list(ai_news_df, 'keywords')
# ai_news_df = split_into_list(ai_news_df, 'classification')
# car_news_df = split_into_list(car_news_df, 'keywords')
# car_news_df = split_into_list(car_news_df, 'classification')

# ai_keyword_embeddings = get_embedding_dict(ai_news_df, 'keywords')
# ai_classification_embeddings = get_embedding_dict(ai_news_df, 'classification')
ai_replace_embeddings = get_embedding_dict(ai_news_df, 'replace_no_tags')
# ai_snippet_embeddings = get_embedding_dict(ai_news_df, 'snippet')

# car_keyword_embeddings = get_embedding_dict(car_news_df, 'keywords')
# car_classification_embeddings = get_embedding_dict(car_news_df, 'classification')
car_replace_embeddings = get_embedding_dict(car_news_df, 'replace_no_tags')
# car_snippet_embeddings = get_embedding_dict(car_news_df, 'snippet')

prefix = "../glanos-data/embeddings/"

# with open(f'{prefix}ai_news_keywords.pickle', 'wb') as f:
#     pickle.dump(ai_keyword_embeddings, f)
# with open(f'{prefix}ai_news_classification.pickle', 'wb') as f:
#     pickle.dump(ai_classification_embeddings, f)
with open(f'{prefix}ai_news_replace_no_tags.pickle', 'wb') as f:
    pickle.dump(ai_replace_embeddings, f)
# with open(f'{prefix}ai_news_snippet.pickle', 'wb') as f:
#     pickle.dump(ai_snippet_embeddings, f)

# with open(f'{prefix}car_news_keywords.pickle', 'wb') as f:
#     pickle.dump(car_keyword_embeddings, f)
# with open(f'{prefix}car_news_classification.pickle', 'wb') as f:
#     pickle.dump(car_classification_embeddings, f)
with open(f'{prefix}car_news_replace_no_tags.pickle', 'wb') as f:
    pickle.dump(car_replace_embeddings, f)
# with open(f'{prefix}car_news_snippet.pickle', 'wb') as f:
#     pickle.dump(car_snippet_embeddings, f)

100%|█| 260403/260403 [1:42:19<00:00, 42.42it/
100%|█| 176117/176117 [1:22:16<00:00, 35.67it/


In [5]:
df = split_into_list(df, 'keywords')
df = split_into_list(df, 'classification')
df

/Users/bartekjezierski/Desktop/master-thesis/notebooks/utils.py:196: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

/Users/bartekjezierski/Desktop/master-thesis/notebooks/utils.py:196: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



tooltip  score   
0       (2023-04-21) Strategy|Company Info\n\nat KPMG ...    1.0  \
1       (2023-04-21) Leadership\n\nLatentView has been...    1.0   
2       (2023-04-21) \n\nIn his last role, Prashant wa...    0.8   
3       (2023-04-21) \n\nWe're proud of the end result...    0.8   
4       (2023-04-21) Market Share Growth\n\nWipro cons...    1.0   
...                                                   ...    ...   
452489                                                NaN    NaN   
452490                                                NaN    NaN   
452491                                                NaN    NaN   
452492                                                NaN    NaN   
452493                                                NaN    NaN   

                                                  snippet   id   
0       at KPMG where he focused on complex financial ...  ID0  \
1       LatentView has been recognized as an industry ...  ID1   
2       In his last role, Prashant was playing the rol...  ID2   
3       We're proud of the end result of this implemen...  ID3   
4       Wipro consolidates presence in foods with acqu...  ID4   
...                                                   ...  ...   
452489  BMW’s premium hatchback will get a complete re...  NaN   
452490  Volkswagen has announced a new limited edition...  NaN   
452491  Volkswagen’s premium SUV, the Touareg, is now ...  NaN   
452492  The VW Touareg is available in Elegance, Black...  NaN   
452493  too – features such as autonomous emergency br...  NaN   

                                                embedding   
0       [0.06154659017920494, 0.08247778564691544, -0....  \
1       [-0.017490660771727562, -0.036421071738004684,...   
2       [0.07539796829223633, -0.025188380852341652, -...   
3       [-0.030860286206007004, 0.047984544187784195, ...   
4       [0.08279228955507278, 0.027778802439570427, -0...   
...                                                   ...   
452489                                                NaN   
452490                                                NaN   
452491                                                NaN   
452492                                                NaN   
452493                                                NaN   

                            company      relationEntity relationEntityType   
0                          KPMG A/S                 NaN                NaN  \
1                      Gartner Inc.                 NaN                NaN   
2                   Infosys Limited  Prashant Ramanujan             person   
3       Fti Consulting Inc. Holding      Palmer Richard             person   
4                     Wipro Limited                 NaN                NaN   
...                             ...                 ...                ...   
452489                          NaN                 NaN                NaN   
452490                          NaN                 NaN                NaN   
452491                          NaN                 NaN                NaN   
452492                          NaN                 NaN                NaN   
452493                          NaN                 NaN                NaN   

                  classification country   
0       [strategy, company info]      US  \
1                   [leadership]      IN   
2                             []      JO   
3                             []      IE   
4          [market share growth]      IN   
...                          ...     ...   
452489                  [entity]     NaN   
452490                  [entity]     NaN   
452491                  [entity]     NaN   
452492                  [entity]     NaN   
452493                  [entity]     NaN   

                                                 keywords   
0                                                    [he]  \
1                               [leader, industry leader]   
2         [head, leader, role, key leader, regional head] 

In [20]:
keyword_embeddings = get_embedding_dict(df, 'keywords')
keyword_embeddings

100%|████████████████████████████████████████████████████████████| 8446/8446 [02:23<00:00, 58.88it/s]


{'symposium': array([ 5.72200753e-02, -4.02924456e-02,  5.96816055e-02,  3.42908464e-02,
        -8.94022360e-03,  1.12996381e-02, -2.40549687e-02,  7.84958806e-03,
        -9.38980095e-03, -3.07339206e-02,  2.49474496e-02,  4.93322173e-03,
        -1.16815008e-02,  3.15094218e-02, -5.42367734e-02, -1.50661711e-02,
         1.93504654e-02,  2.38831453e-02,  4.18237709e-02, -1.17183933e-02,
        -1.32323541e-02, -3.63192111e-02, -1.23512642e-02,  3.83334346e-02,
        -7.20103970e-03, -3.28007862e-02, -8.05866271e-02, -5.39989024e-02,
         3.39472368e-02,  2.19036005e-02, -6.33679703e-02, -2.24919431e-02,
        -2.54115835e-02,  5.81958005e-03,  8.68708082e-03,  7.92302340e-02,
         6.65829331e-02,  1.52919358e-02,  8.27255752e-03,  1.89588033e-02,
        -5.81049286e-02, -3.02670319e-02,  7.70640597e-02, -3.23222466e-02,
         5.08007966e-03, -2.39173658e-02, -4.39845547e-02, -2.26751454e-02,
        -7.41447583e-02, -4.39486057e-02, -6.18142483e-04, -9.58618596e-02,

In [21]:
classification_embeddings = get_embedding_dict(df, 'classification')

100%|██████████████████████████████████████████████████████████████| 532/532 [00:15<00:00, 35.13it/s]


In [5]:
relation_entity_embeddings = get_embedding_dict(big_consulting_df, 'relationEntity')

TypeError: 'float' object is not iterable

In [22]:
prefix = "../glanos-data/embeddings/"
# with open(f'{prefix}re_embedding_dict.pickle', 'wb') as f:
#     pickle.dump(relation_entity_embeddings, f)
with open(f'{prefix}kw_embedding_dict.pickle', 'wb') as f:
    pickle.dump(keyword_embeddings, f)

In [23]:
with open(f'{prefix}class_embedding_dict.pickle', 'wb') as f:
    pickle.dump(classification_embeddings, f)

In [8]:
'''
Build embeddings from consulting data 2 without replace tags
'''
big_consulting_df = pd.read_csv('../glanos-data/datasets/big_consulting_export_replace.tsv', delimiter='\t')
big_consulting_df = create_replace_no_tags_col(big_consulting_df)
replace_embeddings = get_embedding_dict(big_consulting_df, 'replace_no_tags')
prefix = "../glanos-data/embeddings/"

with open(f'{prefix}big_consulting_2_replace_no_tags.pickle', 'wb') as f:
    pickle.dump(replace_embeddings, f)


100%|█████| 5206/5206 [01:41<00:00, 51.25it/s]


In [9]:
'''
Build embeddings from consulting data 2 from normal snippets
'''
big_consulting_df = pd.read_csv('../glanos-data/datasets/big_consulting_export_replace.tsv', delimiter='\t')
embeddings = get_embedding_dict(big_consulting_df, 'snippet')
prefix = "../glanos-data/embeddings/"

with open(f'{prefix}big_consulting_2_snippet.pickle', 'wb') as f:
    pickle.dump(embeddings, f)


100%|█████████| 6154/6154 [02:04<00:00, 49.46it/s]
